## Loading Dataset

In [1]:
import numpy as np
import pandas as pd

In [ ]:
X_fn = "./data/combine_astii_astiii_filter_all_smoothing_ipm_K_pneumonia_norm.npy"
y_fn = "./data/y_astii_astiii_filter_all_ipm_K_pneumonia.npy"
patient_fn = "./data/patient_astii_astiii_filter_all_ipm_K_pneumonia.npy"
X_train_raw = np.load(X_fn,allow_pickle=True)
y_train_raw = np.load(y_fn,allow_pickle=True)
patient_train_raw = np.load(patient_fn,allow_pickle=True)

classnames=['CR K_pneumonia','CS K_pneumonia']


df_p = pd.DataFrame(X_train_raw)
df_p['Classes'] = y_train_raw
df_p['Patient_ID'] = patient_train_raw 


In [3]:
if not isinstance(X_train_raw, np.ndarray):
    X_train_raw = np.array(X_train_raw, dtype=np.float32)
elif X_train_raw.dtype != np.float32:
    X_train_raw = X_train_raw.astype(np.float32)

### Model Setting

In [4]:
# model
from model import Variant_LeNet,ResNet,RamanNet,ViT
from tqdm import tqdm
import torch
import pandas as pd
import torch.nn as nn
from torch.autograd import Variable
from losses import FocalLoss
from losses import AdaptiveProxyAnchorLoss
from imblearn.metrics import specificity_score
from sklearn.metrics import (
    confusion_matrix,
    accuracy_score,
    precision_score,
    recall_score,
    f1_score,
    auc,
    roc_curve,
)
from pytorchtools import EarlyStopping
import torch.optim as optim
# Plot
from plot import plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve, plot_heatmap,plot_tsne_interactive_html
import matplotlib.pyplot as plt

import seaborn as sns
from sklearn.metrics import confusion_matrix
from config import ORDER, STRAINS
import math

# Training setting
n_classes = 2
epochs = 300 
batch_size = 256
num = 50
num_workers = 7


C_total = np.zeros((n_classes, n_classes))
C = np.zeros((n_classes, n_classes))
C_new = np.zeros((n_classes, n_classes))

2025-07-22 17:03:58.467497: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-07-22 17:03:58.467526: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-07-22 17:03:58.468180: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


## LeNet + CE

In [5]:


class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion = nn.CrossEntropyLoss(weight=alpha).cuda()
        self.get_num_labeled_class = 2
        self.optimizer = optim.Adam(self.net.parameters(),lr = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
            inputs, targets,patients = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device), patients
            out,emb= self.net(inputs)
            
            loss = self.criterion(out, targets)
            
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 


        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                         "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
                inputs, targets ,patients = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda'), patients
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            patient_ids = np.concatenate( patient_ids, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
                patient_ids,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets,train_patient_ids = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            print("class", i, accuracy_score(y_true[idx], y_pred[idx]))

        return (
            confusion_matrix(y_true, y_pred),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            train_patient_ids,
            test_patient_ids
        )

In [6]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

# metrics
lenet_train_avg_accuracy = []
lenet_avg_accuracy = []
lenet_avg_roc = []

selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []

        if i == 23:
            i =50

        if i == 35:
            i =51

        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = spectral_dataloader(
                            X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                        )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = Variant_LeNet(in_channels=1, out_channels=n_classes)

    model_path = f"best_variant_lenet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    lenet_train_avg_accuracy.append(train_acc)
    lenet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"variant_lenet_best_test_accuracy_combined_train",f"variant_lenet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"variant_lenet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"variant_lenet_low_test_accuracy_combined_train",f"variant_lenet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"variant_lenet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    lenet_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"variant_lenet_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"variant_lenet_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"variant_lenet_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.458 | acc: 68.06% (2124/3121)


  0%|          | 1/300 [00:00<02:48,  1.77it/s]


epoch 1: test average loss: 0.454 | acc: 44.44% (80/180)
best test acc found

epoch 2: train average loss: 0.313 | acc: 80.17% (2502/3121)


...


epoch 42: test average loss: 0.695 | acc: 76.73% (122/159)
EarlyStopping counter: 24/25 (best: 0.9182)

epoch 43: train average loss: 0.071 | acc: 100.00% (3142/3142)


 14%|█▍        | 42/300 [00:19<02:00,  2.14it/s]


epoch 43: test average loss: 0.800 | acc: 71.07% (113/159)
EarlyStopping counter: 25/25 (best: 0.9182)
🔴 Early stopping triggered
load model at epoch 18, with test acc : 0.918



/tmp/ipykernel_955447/474861799.py:156: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.9182389937106918
class 0 0.8860759493670886
class 1 0.95
                            0
Accuracy               0.9182
Recall         [0.8861, 0.95]
Specificity    [0.95, 0.8861]
Precision    [0.9459, 0.8941]
F1 Score      [0.915, 0.9212]


In [7]:
print("max test acc:", np.max(lenet_avg_accuracy))
print("min test acc:", np.min(lenet_avg_accuracy))

print("train mean:", np.mean(lenet_train_avg_accuracy))
print("train std:", np.std(lenet_train_avg_accuracy))

    
print("mean:", np.mean(lenet_avg_accuracy))
print("std:", np.std(lenet_avg_accuracy))

    
print("auc mean:", np.mean(lenet_avg_roc))
print("auc std:", np.std(lenet_avg_roc))
    

max test acc: 1.0
min test acc: 0.5111111111111111
train mean: 0.965181872247787
train std: 0.049342630531195274
mean: 0.8175933198653845
std: 0.1487547958061133
auc mean: 0.8592732675498234
auc std: 0.17957206925178112


## ResNet + CE

In [8]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

resnet_train_avg_accuracy = []
resnet_avg_accuracy = []
resnet_avg_roc = []


selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []

        if i == 23:
            i =50

        if i == 35:
            i =51

        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    # setting resnet
    layers = 6
    hidden_size = 100
    block_size = 2
    hidden_sizes = [hidden_size] * layers
    num_blocks = [block_size] * layers
    input_dim = 400
    model = ResNet(
                    hidden_sizes,
                    num_blocks,
                    input_dim=input_dim,
                    in_channels=64,
                    n_classes=2,
                )

    model_path = f"best_resnet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    resnet_train_avg_accuracy.append(train_acc)
    resnet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"resnet_best_test_accuracy_combined_train",f"resnet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"resnet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"resnet_low_test_accuracy_combined_train",f"resnet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"resnet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    resnet_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"resnet_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"resnet_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"resnet_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.601 | acc: 72.03% (2248/3121)


  0%|          | 1/300 [00:00<04:08,  1.20it/s]


epoch 1: test average loss: 0.515 | acc: 44.44% (80/180)
best test acc found

epoch 2: train average loss: 0.471 | acc: 91.09% (2843/3121)


...


epoch 35: test average loss: 4.507 | acc: 49.69% (79/159)
EarlyStopping counter: 24/25 (best: 0.7987)

epoch 36: train average loss: 0.050 | acc: 98.57% (3097/3142)


 12%|█▏        | 35/300 [00:26<03:21,  1.31it/s]


epoch 36: test average loss: 4.343 | acc: 49.06% (78/159)
EarlyStopping counter: 25/25 (best: 0.7987)
🔴 Early stopping triggered
load model at epoch 11, with test acc : 0.799



/tmp/ipykernel_955447/474861799.py:156: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.7987421383647799
class 0 0.620253164556962
class 1 0.975
                            0
Accuracy               0.7987
Recall        [0.6203, 0.975]
Specificity   [0.975, 0.6203]
Precision    [0.9608, 0.7222]
F1 Score     [0.7538, 0.8298]


In [9]:
print("max test acc:", np.max(resnet_avg_accuracy))
print("min test acc:", np.min(resnet_avg_accuracy))

print("train mean:", np.mean(resnet_train_avg_accuracy))
print("train std:", np.std(resnet_train_avg_accuracy))

    
print("mean:", np.mean(resnet_avg_accuracy))
print("std:", np.std(resnet_avg_accuracy))

    
print("auc mean:", np.mean(resnet_avg_roc))
print("auc std:", np.std(resnet_avg_roc))
    

max test acc: 0.9894179894179894
min test acc: 0.5888888888888889
train mean: 0.9478723033442675
train std: 0.0598856335961671
mean: 0.8212813266404763
std: 0.13574816710896903
auc mean: 0.8440770805684948
auc std: 0.19608692493660457


## RamanNet + CE

In [10]:

from datasets_sliding_window import sliding_spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

ramannet_train_avg_accuracy = []
ramannet_avg_accuracy = []
ramannet_avg_roc = []


selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []

        if i == 23:
            i =50

        if i == 35:
            i =51

        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = sliding_spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = sliding_spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = RamanNet(w_len=50, n_windows=14,n_classes=2)

    model_path = f"best_ramannet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    ramannet_train_avg_accuracy.append(train_acc)
    ramannet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"ramannet_best_test_accuracy_combined_train",f"ramannet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"ramannet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"ramannet_low_test_accuracy_combined_train",f"ramannet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"ramannet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    ramannet_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"ramannet_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"ramannet_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"ramannet_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.470 | acc: 71.61% (2235/3121)


  0%|          | 1/300 [00:00<02:51,  1.74it/s]


epoch 1: test average loss: 0.874 | acc: 55.56% (100/180)
best test acc found

epoch 2: train average loss: 0.253 | acc: 90.00% (2809/3121)


...


epoch 34: test average loss: 3.551 | acc: 57.23% (91/159)
EarlyStopping counter: 24/25 (best: 0.7170)

epoch 35: train average loss: 0.017 | acc: 99.08% (3113/3142)


 11%|█▏        | 34/300 [00:19<02:33,  1.74it/s]


epoch 35: test average loss: 1.902 | acc: 70.44% (112/159)
EarlyStopping counter: 25/25 (best: 0.7170)
🔴 Early stopping triggered
load model at epoch 10, with test acc : 0.717



/tmp/ipykernel_955447/474861799.py:156: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.7169811320754716
class 0 0.43037974683544306
class 1 1.0
                            0
Accuracy                0.717
Recall          [0.4304, 1.0]
Specificity     [1.0, 0.4304]
Precision         [1.0, 0.64]
F1 Score     [0.6018, 0.7805]


In [11]:
print("max test acc:", np.max(ramannet_avg_accuracy))
print("min test acc:", np.min(ramannet_avg_accuracy))

print("train mean:", np.mean(ramannet_train_avg_accuracy))
print("train std:", np.std(ramannet_train_avg_accuracy))

    
print("mean:", np.mean(ramannet_avg_accuracy))
print("std:", np.std(ramannet_avg_accuracy))

    
print("auc mean:", np.mean(ramannet_avg_roc))
print("auc std:", np.std(ramannet_avg_roc))

max test acc: 0.9947089947089947
min test acc: 0.3721973094170404
train mean: 0.9430559715928548
train std: 0.08644562650025535
mean: 0.7416385141419509
std: 0.16377843082869323
auc mean: 0.7899556634201856
auc std: 0.24743396981557036


## ViT+CE

In [13]:
class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion = nn.CrossEntropyLoss(weight=alpha).cuda()
        self.get_num_labeled_class = 2
        self.optimizer = optim.Adam(self.net.parameters(),lr = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets) in enumerate(dataloader):
            inputs, targets = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device)
            out,emb= self.net(inputs)
            
            loss = self.criterion(out, targets)
            
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 


        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                         "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets) in enumerate(dataloader):
                inputs, targets = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda')
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            print("class", i, accuracy_score(y_true[idx], y_pred[idx]))

        return (
            confusion_matrix(y_true, y_pred),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
        )

In [15]:
from sklearn.model_selection import StratifiedKFold
import torch.utils.data as Data
from plot import plot_tsne
best_test_accuracy = 0
low_test_accuracy = 1

ViT_train_avg_accuracy = []
ViT_avg_accuracy = []
ViT_avg_roc = []


selected_patient_combinations = set()
    
for i in range(num):

    if i == 23:
        i =50

    if i == 35:
        i =51
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

         # 當前迭代的訓練集和測試集病患
    max_attempts = 100  # 最大嘗試次數
    combination_found = False  # 記錄是否找到新組合

    for attempt in range(max_attempts):
        test_patients = []
        train_patients = []

        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]

            combination_found = True
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)
    
    # Set up dataloaders
    X_train = torch.from_numpy(X_train.astype(np.float32))
    y_train = torch.from_numpy(y_train.astype(np.longlong))


    if isinstance(X_test, np.ndarray):
        X_test = torch.from_numpy(X_test).float()
    else:
        X_test = X_test.float()  # 如果 X_test 已經是張量

    if isinstance(y_test, np.ndarray):
        y_test = torch.from_numpy(y_test).long()
    else:
        y_test = y_test.long()  # 如果 y_test 已經是張量


    dataset_tr = Data.TensorDataset(X_train, y_train)
    dl_tr = Data.DataLoader(dataset_tr, batch_size=batch_size, shuffle = True)
        
        
    dataset_test = Data.TensorDataset(X_test, y_test)
    dl_test = Data.DataLoader(dataset_test, batch_size=batch_size, shuffle = False)
    
    values, counts = np.unique(np.asarray(y_test), return_counts=True)

    dataloaders = {"train": dl_tr, "test": dl_test}

    model = ViT(image_size = (1,400), patch_size = (1, 16), num_classes = n_classes, channels = 1, dim = 64, depth = 3, heads = 6, mlp_dim = 128, dropout = 0.1, emb_dropout = 0.1)

    model_path = f"best_ViT_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined = solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    ViT_train_avg_accuracy.append(train_acc)
    ViT_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne(f"ViT_best_test_accuracy_combined_train",f"ViT_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets,classnames )
      
        plot_heatmap(f"ViT_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne(f"ViT_low_test_accuracy_combined_train",f"ViT_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets, classnames )
            
        plot_heatmap(f"ViT_low_test_accuracy_heatmap", C,class_names=classnames)
        
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    ViT_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"ViT_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"ViT_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"ViT_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 1/300 [00:00<00:36,  8.21it/s]


epoch 1: train average loss: 0.694 | acc: 52.36% (1634/3121)

epoch 1: test average loss: 0.655 | acc: 44.44% (80/180)
best test acc found


  1%|          | 2/300 [00:00<00:35,  8.37it/s]


epoch 2: train average loss: 0.643 | acc: 60.78% (1897/3121)

epoch 2: test average loss: 0.726 | acc: 75.00% (135/180)
best test acc found


...

 12%|█▏        | 36/300 [00:04<00:27,  9.48it/s]


epoch 36: train average loss: 0.096 | acc: 96.21% (3023/3142)

epoch 36: test average loss: 0.476 | acc: 89.94% (143/159)
EarlyStopping counter: 24/25 (best: 0.9686)


 12%|█▏        | 36/300 [00:04<00:30,  8.73it/s]


epoch 37: train average loss: 0.100 | acc: 96.69% (3038/3142)

epoch 37: test average loss: 0.831 | acc: 84.91% (135/159)
EarlyStopping counter: 25/25 (best: 0.9686)
🔴 Early stopping triggered
load model at epoch 12, with test acc : 0.969
total 0.9685534591194969
class 0 0.9493670886075949
class 1 0.9875
                            0
Accuracy               0.9686
Recall       [0.9494, 0.9875]
Specificity  [0.9875, 0.9494]
Precision    [0.9868, 0.9518]
F1 Score     [0.9677, 0.9693]



/tmp/ipykernel_955447/960659495.py:153: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



In [16]:
print("max test acc:", np.max(ViT_avg_accuracy))
print("min test acc:", np.min(ViT_avg_accuracy))

print("train mean:", np.mean(ViT_train_avg_accuracy))
print("train std:", np.std(ViT_train_avg_accuracy))

    
print("mean:", np.mean(ViT_avg_accuracy))
print("std:", np.std(ViT_avg_accuracy))

    
print("auc mean:", np.mean(ViT_avg_roc))
print("auc std:", np.std(ViT_avg_roc))

max test acc: 0.9798994974874372
min test acc: 0.3542600896860987
train mean: 0.8428916070801062
train std: 0.144598131032246
mean: 0.7907590994614769
std: 0.16495876565171685
auc mean: 0.8006312527562399
auc std: 0.236359241808048


## LeNet + MAPA + Focal

In [17]:
class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion_proxy =AdaptiveProxyAnchorLoss(nb_classes=n_classes, sz_embed=256, mrg=0.5, alpha=32,\
                                             nb_proxies=1, scale_margin=1).cuda()
        self.criterion = FocalLoss(alpha=alpha, gamma=2).cuda()
        self.get_num_labeled_class = 2
        self.param_groups = [
            {'params': list(set(model.parameters()).difference(set(model.embedding.parameters())))},
            {'params': model.embedding.parameters() , 'lr':float(0.001) * 1},
            {'params': self.criterion_proxy.mrg,'lr':float(0.001) },
            {'params': self.criterion_proxy.proxies, 'lr':float(0.001) * 100}
        ]
        self.optimizer =torch.optim.AdamW(self.param_groups, lr=0.001, weight_decay = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
        total_proxy_loss = 0
        total_crossentropy_loss = 0
            
        for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
            inputs, targets,patients = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device), patients
            #print(inputs.shape)
            out,emb= self.net(inputs)
            
            loss1 = self.criterion(out, targets)
            loss2 = self.criterion_proxy(emb, targets)
            loss = loss1 + 0.5 * loss2
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()
                torch.nn.utils.clip_grad_value_(self.net.parameters(), 10)
                torch.nn.utils.clip_grad_value_(self.criterion_proxy.parameters(), 10)


            total_loss += loss.item()
            total_proxy_loss += loss2.item()
            total_crossentropy_loss += loss1.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 

        self.scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(self.optimizer, T_max=60)

        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                         "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)
                
                self.scheduler.step()

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
                inputs, targets ,patients = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda'), patients
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            patient_ids = np.concatenate( patient_ids, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
                patient_ids,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets,train_patient_ids = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            print("class", i, accuracy_score(y_true[idx], y_pred[idx]))

        return (
            confusion_matrix(y_true, y_pred),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            train_patient_ids,
            test_patient_ids
        )

In [18]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

# metrics
lenet_mapa_focal_train_avg_accuracy = []
lenet_mapa_focal_avg_accuracy = []
lenet_mapa_focal_avg_roc = []

selected_patient_combinations = set()
    
for i in range(num):
    # Initialize empty DataFrames for this iteration's train and test sets
    train_data = pd.DataFrame(columns=df_p.columns)
    test_data = pd.DataFrame(columns=df_p.columns)

    # 當前迭代的訓練集和測試集病患
    max_attempts = 300 # 最大嘗試次數

    for attempt in range(max_attempts):
            
        test_patients = []
        train_patients = []

        if i == 23:
            i =50

        if i == 35:
            i =51

        
        for class_label, group in df_p.groupby('Classes'):
                # Select one random patient for the test set and the rest for the train set
            num_patients = group['Patient_ID'].nunique()  # Number of unique patients in this class
            test_patient_count = 1
                
            selected_test_patients = group['Patient_ID'].sample(n=test_patient_count, random_state=i).unique()
            test_patients.extend(selected_test_patients)
                
            selected_train_patients = set(group['Patient_ID'].unique()) - set(selected_test_patients)
            train_patients.extend(selected_train_patients)

        patient_combination = (tuple(sorted(train_patients)), tuple(sorted(test_patients)))
                    

        # 檢查組合是否已存在
        if patient_combination not in selected_patient_combinations:
                
            selected_patient_combinations.add(patient_combination)

            test_data = df_p[df_p['Patient_ID'].isin(test_patients)]
            train_data = df_p[df_p['Patient_ID'].isin(train_patients)]
            
            break


    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)
            

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = Variant_LeNet(in_channels=1, out_channels=n_classes)

    model_path = f"best_variant_lenet_mapa_focal_model_{i}.pth"

    class_counts = np.bincount(y_train)
    num_classes = len(class_counts)
    total_samples = len(y_train)

    class_weights = []
    for count in class_counts:
        weight = 1 / (count / total_samples)
        class_weights.append(weight)
    class_weights = torch.FloatTensor(class_weights)
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    lenet_mapa_focal_train_avg_accuracy.append(train_acc)
    lenet_mapa_focal_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"lenet_mapa_focal_best_test_accuracy_combined_train",f"lenet_mapa_focal_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"lenet_mapa_focal_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"lenet_mapa_focal_low_test_accuracy_combined_train",f"lenet_mapa_focal_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"lenet_mapa_focal_low_test_accuracy_heatmap", C,class_names=classnames)
        
    fpr = dict()
    tpr = dict()
    roc_auc = dict()
    for i in range(np.unique(y_true).shape[0]):
        fpr[i], tpr[i], _ = roc_curve(y_test == i, y_pred_prob[:, i])
        roc_auc[i] = auc(fpr[i], tpr[i])
    values = [
            v
            for v in roc_auc.values()
            if isinstance(v, (int, float)) and not math.isnan(v)
    ]
    if values:
        auc_score = sum(values) / len(values)
    lenet_mapa_focal_avg_roc.append(auc_score)

    for i in range(n_classes):
        C_new[i] = np.round((C[i] / (counts[i] * num)), 2)

        # Plot confusion matrix
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]
    cm = 100 * C_new / C_new.sum(axis=1)[:, np.newaxis]

        # calculate comfusion matrix
    accuracy = accuracy_score(y_true, y_pred)
    sensitivity = recall_score(y_true, y_pred, average="micro", zero_division=0)
    specificity = cm[1, 1] / (cm[1, 0] + cm[1, 1])
    f1 = f1_score(y_true, y_pred, average="micro", zero_division=0)

    # metrices result
    df = pd.DataFrame(
        {
            "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
            "Recall": [
                    recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
            "Precision": [
                    precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            "F1 Score": [
                    f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                ],
            }
    )
    print(df.transpose())

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"lenet_mapa_focal_{i}_roc_curve", y_true, y_test, y_pred_prob)

    plot_heatmap(f"lenet_mapa_focal_{i}_heatmap", cm,class_names=classnames)

plot_heatmap(f"lenet_mapa_focal_average_heatmap", C_total,class_names=classnames)


1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 32.458 | acc: 60.21% (1879/3121)


  0%|          | 1/300 [00:00<03:08,  1.58it/s]


epoch 1: test average loss: 28.106 | acc: 44.44% (80/180)
best test acc found

epoch 2: train average loss: 26.244 | acc: 69.88% (2181/3121)


...


epoch 53: test average loss: 16.987 | acc: 97.48% (155/159)
EarlyStopping counter: 24/25 (best: 0.9937)

epoch 54: train average loss: 2.050 | acc: 99.01% (3111/3142)


 18%|█▊        | 53/300 [00:31<02:27,  1.67it/s]


epoch 54: test average loss: 16.883 | acc: 97.48% (155/159)
EarlyStopping counter: 25/25 (best: 0.9937)
🔴 Early stopping triggered
load model at epoch 29, with test acc : 0.994



/tmp/ipykernel_955447/1054042983.py:175: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 0.9937106918238994
class 0 1.0
class 1 0.9875
                            0
Accuracy               0.9937
Recall          [1.0, 0.9875]
Specificity     [0.9875, 1.0]
Precision       [0.9875, 1.0]
F1 Score     [0.9937, 0.9937]


In [19]:
print("max test acc:", np.max(lenet_mapa_focal_avg_accuracy))
print("min test acc:", np.min(lenet_mapa_focal_avg_accuracy))

print("train mean:", np.mean(lenet_mapa_focal_train_avg_accuracy))
print("train std:", np.std(lenet_mapa_focal_train_avg_accuracy))

    
print("mean:", np.mean(lenet_mapa_focal_avg_accuracy))
print("std:", np.std(lenet_mapa_focal_avg_accuracy))

    
print("auc mean:", np.mean(lenet_mapa_focal_avg_roc))
print("auc std:", np.std(lenet_mapa_focal_avg_roc))

max test acc: 1.0
min test acc: 0.59375
train mean: 0.8927389822577757
train std: 0.0799012282207574
mean: 0.8689300872922623
std: 0.13916920677593603
auc mean: 0.8790787428906449
auc std: 0.19807712880808082


In [21]:
import numpy as np

# 將模型名稱與對應數據組成字典，便於迴圈處理
models = {
    "LeNet + MAPA + Focal": lenet_mapa_focal_avg_accuracy,
    "RamanNet + CE": ramannet_avg_accuracy,
    "LeNet + CE": lenet_avg_accuracy,
    "ResNet + CE": resnet_avg_accuracy,
    "ViT + CE": ViT_avg_accuracy
}

# 輸出結果
print("Model Comparison (Mean ± Std):")
for name, acc in models.items():
    mean_acc = np.mean(acc)
    std_acc = np.std(acc)
    print(f"{name:<20}: {mean_acc:.4f} ± {std_acc:.4f}")


Model Comparison (Mean ± Std):
LeNet + MAPA + Focal: 0.8689 ± 0.1392
RamanNet + CE       : 0.7416 ± 0.1638
LeNet + CE          : 0.8176 ± 0.1488
ResNet + CE         : 0.8213 ± 0.1357
ViT + CE            : 0.7908 ± 0.1650
